In [ ]:
import numpy
import bark
import scipy
import torch
import nltk

print(f"Numpy version: {numpy.__version__}")
# The 'bark' module does not have a __version__ attribute.
# print(f"Bark version: {bark.__version__}")
print(f"PyTorch version: {torch.__version__}")
print(f"Scipy version: {scipy.__version__}")
print(f"NLTK version: {nltk.__version__}")

Numpy version: 2.0.2
PyTorch version: 2.9.0+cu126
Scipy version: 1.16.3
NLTK version: 3.9.1


# **Latihan Awal**

In [ ]:
import torch

if torch.cuda.is_available():
    print(f"CUDA version: {torch.version.cuda}")
else:
    print("CUDA is not available on this system.")

CUDA version: 12.6


In [ ]:
!pip install git+https://github.com/suno-ai/bark.git -q
!pip install scipy -q

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 49.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.5/14.5 MB 39.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 4.2 MB/s eta 0:00:00


In [ ]:
import os
import torch
from bark import SAMPLE_RATE, generate_audio, preload_models
from IPython.display import Audio
from scipy.io.wavfile import write as write_wav
import numpy as np

/usr/local/lib/python3.12/dist-packages/torch/backends/__init__.py:46: UserWarning: Please use the new API settings to control TF32 behavior, such as torch.backends.cudnn.conv.fp32_precision = 'tf32' or torch.backends.cuda.matmul.fp32_precision = 'ieee'. Old settings, e.g, torch.backends.cuda.matmul.allow_tf32 = True, torch.backends.cudnn.allow_tf32 = True, allowTF32CuDNN() and allowTF32CuBLAS() will be deprecated after Pytorch 2.9. Please see https://pytorch.org/docs/main/notes/cuda.html#tensorfloat-32-tf32-on-ampere-and-later-devices (Triggered internally at /pytorch/aten/src/ATen/Context.cpp:80.)
  self.setter(val)


In [ ]:
default_load = torch.load

# Fungsi bypass agar model bark bisa dimuat oleh Pytorch versi 2.6
def safe_load_bypass(*args, **kwargs):
    # Memaksa weights_only=False agar model Bark (numpy types) bisa dibaca
    if 'weights_only' not in kwargs:
        kwargs['weights_only'] = False
    return default_load(*args, **kwargs)

# Terapkan patch
torch.load = safe_load_bypass

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

# Preload model ~2GB
preload_models()

text_2.pt:   0%|          | 0.00/5.35G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

coarse_2.pt:   0%|          | 0.00/3.93G [00:00<?, ?B/s]

fine_2.pt:   0%|          | 0.00/3.74G [00:00<?, ?B/s]

/usr/local/lib/python3.12/dist-packages/torch/nn/utils/weight_norm.py:144: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


Downloading: "https://dl.fbaipublicfiles.com/encodec/v0/encodec_24khz-d7cc33bc.th" to /root/.cache/torch/hub/checkpoints/encodec_24khz-d7cc33bc.th



  0%|          | 0.00/88.9M [00:00<?, ?B/s]
  0%|          | 128k/88.9M [00:00<03:53, 399kB/s]
  0%|          | 256k/88.9M [00:00<02:44, 563kB/s]
  0%|          | 384k/88.9M [00:00<02:23, 648kB/s]
  1%|          | 768k/88.9M [00:00<01:13, 1.25MB/s]
  2%|▏         | 1.62M/88.9M [00:00<00:34, 2.67MB/s]
  4%|▎         | 3.12M/88.9M [00:01<00:18, 4.87MB/s]
  7%|▋         | 6.25M/88.9M [00:01<00:09, 9.58MB/s]
 12%|█▏        | 10.2M/88.9M [00:01<00:05, 14.3MB/s]
 15%|█▌        | 13.8M/88.9M [00:01<00:04, 16.7MB/s]
 20%|█▉        | 17.5M/88.9M [00:01<00:03, 18.8MB/s]
 24%|██▍       | 21.4M/88.9M [00:01<00:03, 20.4MB/s]
 28%|██▊       | 25.1M/88.9M [00:02<00:03, 21.3MB/s]
 32%|███▏      | 28.9M/88.9M [00:02<00:02, 22.0MB/s]
 37%|███▋      | 32.8M/88.9M [00:02<00:02, 22.5MB/s]
 41%|████      | 36.5M/88.9M [00:02<00:02, 22.8MB/s]
 45%|████▌     | 40.4M/88.9M [00:02<00:02, 23.1MB/s]
 50%|████▉     | 44.1M/88.9M [00:03<00:02, 23.2MB/s]
 54%|█████▍    | 48.0M/88.9M [00:03<00:01, 23.5MB/s]
 58%|███

In [ ]:
# Latihan dasar membuat narasi pendek

text_prompt = "Hello, everyone! Welcome to the audio generation workshop. Today we're learning Bark."

# Generate Audio
audio_array = generate_audio(text_prompt)

# Putar Audio di Notebook
Audio(audio_array, rate=SAMPLE_RATE)

100%|██████████| 18/18 [00:21<00:00,  1.18s/it]


In [ ]:
text_prompt = "Wow, cool, now you can change the sound style produced by Bark. Try other speaker presets."

speaker_preset = "v2/en_speaker_9" # Coba ganti angkanya 0-9

audio_array = generate_audio(text_prompt, history_prompt=speaker_preset)

Audio(audio_array, rate=SAMPLE_RATE)

100%|██████████| 34/34 [00:46<00:00,  1.36s/it]


In [ ]:
# Gunakan tags seperti [laughs], [sighs], [gasps], [clears throat], ...

# Contoh skenario drama
text_drama = """
[clears throat] Ahem, excuse me.
I can't believe you did that! [laughs]
That's hilarious, but... [sighs] also a little dangerous.
"""
audio_drama = generate_audio(text_drama, history_prompt="v2/en_speaker_2")

Audio(audio_drama, rate=SAMPLE_RATE)

100%|██████████| 35/35 [00:43<00:00,  1.24s/it]


In [ ]:
# Tambahkan simbol ♪ di awal dan akhir untuk memicu mode musik.

# Contoh lirik lagu
text_song = """
♪ Dear God the only thing I ask of you is
to hold her when I'm not around. ♪
"""

audio_song = generate_audio(text_song)

Audio(audio_song, rate=SAMPLE_RATE)

100%|██████████| 37/37 [00:44<00:00,  1.21s/it]


In [ ]:
filename = "hasil_bark_latihan.wav"

# Normalisasi audio agar volumenya pas
scaled = np.int16(audio_song / np.max(np.abs(audio_song)) * 32767)

write_wav(filename, SAMPLE_RATE, scaled)

# Download file ke komputer lokal (khusus Colab)
from google.colab import files
files.download(filename)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# **Latihan Lanjutan**

In [ ]:
import nltk
nltk.download('punkt_tab')
from bark.generation import generate_text_semantic
from bark.api import semantic_to_waveform
from IPython.display import Audio, display

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [ ]:
def generate_long_audio(text, history_prompt="v2/en_speaker_6", silence_secs=0.25):
    # 1. Pecah teks menjadi kalimat
    sentences = nltk.sent_tokenize(text)
    full_audio = []
    silence = np.zeros(int(silence_secs * SAMPLE_RATE)) # Membuat array hening

    print(f"Total kalimat: {len(sentences)}")

    # 2. Loop per kalimat
    for i, sentence in enumerate(sentences):
        print(f"Sedang memproses kalimat {i+1}")

        # Generate audio per kalimat
        audio_array = generate_audio(sentence, history_prompt=history_prompt)

        # 3. Gabungkan (Stitch)
        full_audio.append(audio_array)
        full_audio.append(silence) # Tambah jeda biar natural

    # Ratakan array menjadi satu dimensi
    return np.concatenate(full_audio)

# --- UJI COBA ---
text_panjang = """
Good morning. This is a fairly long text sample to test your abilities.
Usually, the Bark model will stop working if the text is too long.
However, with the looping algorithm we created, we can make a simple audiobook.
Did you manage to make it?
"""

audio_panjang = generate_long_audio(text_panjang)

# Play
Audio(audio_panjang, rate=SAMPLE_RATE)

Total kalimat: 5
Sedang memproses kalimat 1


100%|██████████| 8/8 [00:09<00:00,  1.22s/it]


Sedang memproses kalimat 2


100%|██████████| 16/16 [00:19<00:00,  1.23s/it]


Sedang memproses kalimat 3


100%|██████████| 12/12 [00:14<00:00,  1.20s/it]


Sedang memproses kalimat 4


100%|██████████| 22/22 [00:26<00:00,  1.22s/it]


Sedang memproses kalimat 5


100%|██████████| 27/27 [00:33<00:00,  1.24s/it]


In [ ]:
host_speaker = "v2/en_speaker_6"   # Pria (Suara Berat)
guest_speaker = "v2/en_speaker_9"  # Wanita (Suara Jernih)

# 2. Skrip Percakapan
# Format: List of Dictionaries
conversation_script = [
    {
        "speaker": host_speaker,
        "text": "Hello listeners! Welcome back to the AI Show. Today we have a special guest. [clears throat]"
    },
    {
        "speaker": guest_speaker,
        "text": "Hi everyone! [laughs] I am so excited to be here."
    },
    {
        "speaker": host_speaker,
        "text": "Tell us, is it true that AI can now speak like humans?"
    },
    {
        "speaker": guest_speaker,
        "text": "Yes, absolutely. Sometimes it is hard to tell the difference. [sighs] It is amazing."
    }
]

# 3. Fungsi Pembuat Podcast
def create_podcast(script):
    full_audio_list = []
    # Membuat array hening selama 0.5 detik untuk jeda antar bicara
    silence = np.zeros(int(SAMPLE_RATE * 0.5))

    for i, line in enumerate(script):
        print(f"   Merekam baris {i+1}")

        # Generate audio per baris
        audio_chunk = generate_audio(
            line['text'],
            history_prompt=line['speaker']
        )

        # Masukkan ke list: Audio -> Silence
        full_audio_list.append(audio_chunk)
        full_audio_list.append(silence)

    # Gabungkan semua potongan menjadi satu file panjang
    final_audio = np.concatenate(full_audio_list)
    return final_audio

# 4. Eksekusi
podcast_audio = create_podcast(conversation_script)

Audio(podcast_audio, rate=SAMPLE_RATE)

   Merekam baris 1


100%|██████████| 23/23 [00:28<00:00,  1.22s/it]


   Merekam baris 2


100%|██████████| 18/18 [00:22<00:00,  1.24s/it]


   Merekam baris 3


100%|██████████| 22/22 [00:27<00:00,  1.25s/it]


   Merekam baris 4


100%|██████████| 35/35 [00:43<00:00,  1.26s/it]


In [ ]:
# @title Hyperparameter Tuning

# Teks yang sama untuk perbandingan
test_text = "I cannot believe what I am seeing. This is absolutely incredible!"
test_speaker = "v2/en_speaker_6"

print(f"📝 Teks Uji: '{test_text}'\n")

# Percobaan 1: Low Temperature
print("1️⃣ Mode Stabil (Temp 0.5)...")
audio_low = generate_audio(
    test_text,
    history_prompt=test_speaker,
    text_temp=0.5,      # Kreativitas rendah
    waveform_temp=0.5   # Variasi gelombang rendah
)
Audio(audio_low, rate=SAMPLE_RATE)

/usr/local/lib/python3.12/dist-packages/bark/generation.py:175: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with InferenceContext(), torch.inference_mode(), torch.no_grad(), autocast():


📝 Teks Uji: 'I cannot believe what I am seeing. This is absolutely incredible!'

1️⃣ Mode Stabil (Temp 0.5)...



100%|██████████| 302/302 [00:06<00:00, 46.39it/s]

100%|██████████| 16/16 [00:18<00:00,  1.18s/it]


In [ ]:
# --- Percobaan 2: Kreatif & Ekspresif (High Temperature) ---
print("\n2️⃣ Mode Kreatif/Liar (Temp 0.9)...")
# Note: Kadang hasilnya sangat bagus (emosional), kadang aneh.
audio_high = generate_audio(
    test_text,
    history_prompt=test_speaker,
    text_temp=0.95,     # Kreativitas tinggi (mendekati batas)
    waveform_temp=0.8
)
Audio(audio_high, rate=SAMPLE_RATE)


2️⃣ Mode Kreatif/Liar (Temp 0.9)...



100%|██████████| 238/238 [00:04<00:00, 51.15it/s]

100%|██████████| 12/12 [00:14<00:00,  1.22s/it]
